In [57]:
import geopandas as gpd
import shapely
import shapely
import rasterio
import glob
import pandas as pd
import numpy as np
from pathlib import Path
import sys
sys.path.append("..")
import os
import datetime
import profiling_tools
import altair as alt
from altair import datum
import json
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# Inputs
Provide:
- Input file path to file with cross section lines/polygons to extract low points/stream profile from
- Output file path where low points will be saved
- Input directory path to location of DEMs
- Parameter `LINE_COMPLEXITY` which is the number of points that each cross-section line is split into. `LINE_COMPLEXITY` elevation points will be extracted from the DEM for each cross section line

If you use the arg, you must run from CLI like this

```
HSFM_GEOMORPH_INPUT_FILE='inputs/mazama_inputs.json' jupyter nbconvert --execute --to html dem-analysis/mt_baker_mass_wasted/transects.ipynb  --output outputs/transects_mazama.html
```

In [58]:

# Or set an env arg:
if os.environ.get('HSFM_GEOMORPH_INPUT_FILE'):
    json_file_path = os.environ['HSFM_GEOMORPH_INPUT_FILE']
else:
    json_file_path = 'inputs/rainbow_inputs.json'

In [59]:
with open(json_file_path, 'r') as j:
     params = json.loads(j.read())

In [60]:
params

{'inputs': {'valley_name': 'Rainbow',
  'TO_DROP': ['1970_09_09',
   '1979_10_06',
   '1987_08_21',
   '1992_09_15',
   '1992_09_18',
   '2013_09_13',
   '2019_10_11'],
  'TO_DROP_LARGER_AREA': ['1970_09_09',
   '1970_09_29',
   '1974_08_10',
   '1979_10_06',
   '1987_08_21',
   '1991_09_09',
   '1992_09_15',
   '1992_09_18',
   '2013_09_13',
   '2019_10_11'],
  'XSECTIONS_INCLUDE': None,
  'erosion_polygon_file': '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/erosion.geojson',
  'erosion_by_date_polygon_file': None,
  'glacier_polygons_file': '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/glaciers.geojson',
  'dems_path': '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems',
  'valley_bounds_file': '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/valley_bounds.geojson',
  'plot_output_dir': '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/plots/',
  'uncertainty_file': 'outputs/uncertainty_rainbow.pc

In [61]:
TO_DROP = params['inputs']['TO_DROP']
input_transects_file = params['transects']['input_transects_file']
input_dems_path = params['inputs']['dems_path']
glacier_polygons_file = params['inputs']['glacier_polygons_file']
LINE_COMPLEXITY = params['transects']['line_complexity']
raster_fns = glob.glob(os.path.join(input_dems_path, "*.tif"))

strip_time_format = params['inputs']['strip_time_format']

reference_dem_date = datetime.datetime.strptime(
    params['inputs']['reference_dem_date'], 
    strip_time_format
)

In [62]:

raster_fns = [fn for fn in raster_fns if Path(fn).stem not in TO_DROP]
raster_fns

['/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1970_09_29.tif',
 '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1974_08_10.tif',
 '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1977_09_27.tif',
 '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1991_09_09.tif',
 '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/2015_09_01.tif',
 '/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1947_09_14.tif']

# Extract profiles from DEMs 

Along each cross-section, extract point with lowest elevation and calculate "path distance", the distance from the furthest downstream cross section line.

In [63]:
# read cross sections file into GeoDataframe
gdf = gpd.read_file(input_transects_file)
# Increase the number of points in each line
gdf.geometry = gdf.geometry.apply(lambda g: profiling_tools.increase_line_complexity(g, LINE_COMPLEXITY))
# Get all points from the cross section lines and create a row for each point. 
gdf['coords'] = gdf.geometry.apply(lambda x: list(x.coords))
crs = gdf.crs
gdf = gpd.GeoDataFrame(pd.DataFrame(gdf).explode('coords', ignore_index=True))
# Make the coords column a shapely.geometry.Point type and drop the cross section geometries which we no longer need.
gdf['coords'] = gdf['coords'].apply(shapely.geometry.Point)
gdf.drop(columns=["geometry"])

combined_gdf = gpd.GeoDataFrame()

for raster in raster_fns:
    print(raster)
    # Extract an elevation value for each point
    with rasterio.open(raster) as src:
        new_gdf = gdf.copy()
        new_gdf['elevation'] = pd.Series([sample[0] for sample in src.sample(new_gdf["coords"].apply(lambda x: (x.xy[0][0], x.xy[1][0])))])
        new_gdf['elevation'] = new_gdf['elevation'].apply(lambda x: np.nan if x == src.nodata else x)

    # Convert file name to datetime as per the provided format
    date = datetime.datetime.strptime(Path(raster).stem, strip_time_format)
    new_gdf['time'] = date

    # Set the geometry to the coords to calculate "path distance"    
    combined_gdf = combined_gdf.append(new_gdf)
combined_gdf.crs = crs
combined_gdf

/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1970_09_29.tif
/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1974_08_10.tif
/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1977_09_27.tif


/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)
/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)
/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)


/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1991_09_09.tif
/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/2015_09_01.tif


/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)
/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)
/tmp/ipykernel_10999/1433347000.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  combined_gdf = combined_gdf.append(new_gdf)


/data2/elilouis/hsfm-geomorph/data/mt_baker_mass_wasted/rainbow/dems/1947_09_14.tif


id                                           geometry  \
0      1  LINESTRING (591408.660 5405195.896, 591409.448...   
1      1  LINESTRING (591408.660 5405195.896, 591409.448...   
2      1  LINESTRING (591408.660 5405195.896, 591409.448...   
3      1  LINESTRING (591408.660 5405195.896, 591409.448...   
4      1  LINESTRING (591408.660 5405195.896, 591409.448...   
...   ..                                                ...   
1495   3  LINESTRING (591624.435 5405902.709, 591624.353...   
1496   3  LINESTRING (591624.435 5405902.709, 591624.353...   
1497   3  LINESTRING (591624.435 5405902.709, 591624.353...   
1498   3  LINESTRING (591624.435 5405902.709, 591624.353...   
1499   3  LINESTRING (591624.435 5405902.709, 591624.353...   

                                           coords    elevation       time  
0     POINT (591408.6597791807 5405195.895568796)  1322.131592 1970-09-29  
1     POINT (591409.4477964417 5405196.182120528)  1321.572998 1970-09-29  
2     POINT (591410.2358137027 5405196.468672259)  1321.088623 1970-09-29  
3      POINT (591411.0238309638 5405196.75522399)  1321.198975 1970-09-29  
4     POINT (591411.8118482247 5405197.041775721)  1320.857178 1970-09-29  
...                                           ...          ...        ...  
1495  POINT (591631.9943374693 5405586.561931659)  1124.028687 1947-09-14  
1496  POINT (591632.2367338573 5405585.962319541)  1124.028687 1947-09-14  
1497  POINT (591632.4791302454 5405585.362707423)  1124.028687 1947-09-14  
1498  POINT (591632.7215266334 5405584.763095305)  1123.481812 1947-09-14  
1499  POINT (591632.9639230215 5405584.163483188)  1123.481812 1947-09-14  

[9000 rows x 5 columns]

In [64]:

for key, group in combined_gdf.groupby(["id", "time"]):
    group.geometry = group['coords']
    group['path_distance'] = pd.Series(group.distance(group.shift(1)).fillna(0)).cumsum()
    new_gdf = new_gdf.append(group)
new_gdf.crs = crs

/home/elilouis/mambaforge/envs/hsfm/lib/python3.9/site-packages/geopandas/array.py:1406: UserWarning: CRS not set for some of the concatenation inputs. Setting output's CRS as WGS 84 / UTM zone 10N (the single non-null crs provided).
  warnings.warn(
/tmp/ipykernel_10999/699848431.py:4: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_gdf = new_gdf.append(group)
/home/elilouis/mambaforge/envs/hsfm/lib/python3.9/site-packages/geopandas/array.py:1406: UserWarning: CRS not set for some of the concatenation inputs. Setting output's CRS as WGS 84 / UTM zone 10N (the single non-null crs provided).
  warnings.warn(
/tmp/ipykernel_10999/699848431.py:4: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  new_gdf = new_gdf.append(group)
/home/elilouis/mambaforge/envs/hsfm/lib/python3.9/site-packages/geopandas/array.py:1406: U

# Mark points as (non)glacial

In [65]:
glaciers_gdf = gpd.read_file(glacier_polygons_file)
glaciers_gdf = glaciers_gdf.to_crs(new_gdf.crs)
glaciers_gdf['time'] = glaciers_gdf['year'].apply(lambda d: datetime.datetime.strptime(d, strip_time_format))

In [66]:
new_gdf['glacial'] = new_gdf.apply(
    lambda row: any(glaciers_gdf.loc[glaciers_gdf['time'] == row["time"], 'geometry'].apply(lambda g: g.contains(row['coords']))),
    axis=1
)

In [67]:
src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).mark_line().encode(
    alt.X("path_distance:Q", scale=alt.Scale(zero=False)),
    alt.Y("elevation:Q", scale=alt.Scale(zero=False)),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 200,
    height = 200
).facet(
    row="id:O"
).resolve_scale(
    x="independent",
    y="independent"
).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
)

alt.FacetChart(...)

In [68]:
src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-8, 8],
    groupby=["id:O"]
).mark_line().encode(
    alt.X("path_distance:Q", scale=alt.Scale(zero=False)),
    alt.Y("rolling_mean:Q", scale=alt.Scale(zero=False)),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 200,
    height = 200
).facet(
    row="id:O"
).resolve_scale(
    x="independent",
    y="independent"
).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
)

alt.FacetChart(...)

## Deming transect 1

In [69]:

src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
src = src.query("id == 1")
src = src.query("path_distance < 80")
alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-3, 3],
    groupby=["id:O"]
).mark_line().encode(
    alt.X("path_distance:Q", title="Distance (m)", scale=alt.Scale(zero=False, domain=[0,80])),
    alt.Y("rolling_mean:Q", title="Elevation (m)", scale=alt.Scale(zero=False, domain=[1140, 1160])),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 200,
    height = 100
).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
)

alt.Chart(...)

## Deming transect 2

In [70]:

src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
src = src.query("id == 2")
alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-3, 3],
    groupby=["id:O"]
).transform_filter(
    alt.datum.path_distance > 2
).transform_filter(
    alt.datum.path_distance < 117
).mark_line().encode(
    alt.X("path_distance:Q", title="Distance (m)", scale=alt.Scale(zero=False, domain=[0,120])),
    alt.Y("rolling_mean:Q", title="Elevation (m)", scale=alt.Scale(zero=False, domain=[1060, 1200])),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 171.5,
    height = 200
).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
)

alt.Chart(...)

## Rainbow transect 1


In [71]:

src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
src = src.query("id == 1")
tran1 = alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-3, 3],
    groupby=["id:O"]
).transform_filter(
    alt.datum.path_distance > 2
).transform_filter(
    alt.datum.path_distance < 400
).mark_line().encode(
    alt.X("path_distance:Q", title="Distance (m)", scale=alt.Scale(zero=False, domain=[0,400], nice=False)),
    alt.Y("rolling_mean:Q", title="Elevation (m)", scale=alt.Scale(zero=False, domain=[1100, 1350], nice=False)),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 320,
    height = 200
)

## Rainbow transect 2

In [78]:

src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
src = src.query("id == 2")
tran2 = alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-5, 5],
    groupby=["id:O"]
).transform_filter(
    alt.datum.path_distance > 2
).transform_filter(
    alt.datum.path_distance < 110
).mark_line().encode(
    alt.X("path_distance:Q", title="Distance (m)", scale=alt.Scale(zero=False, domain=[0,110], nice=False)),
    alt.Y("rolling_mean:Q", title="Elevation (m)", scale=alt.Scale(zero=False, domain=[1290, 1330], nice=False)),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 325,
    height = 200
)

In [79]:
(tran1 | tran2).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
).configure_axis(
    titleColor='black', 
    titleFontSize=14, 
    labelFontSize=16
)

alt.HConcatChart(...)

In [18]:
width = 320, 
height = 200

width_distance = 65
height_distance = 40

In [19]:
320 * 40/65

196.92307692307693

## Rainbow transect 3

In [36]:

src = new_gdf[[ "time", "path_distance", "elevation", "id", "glacial"]].reset_index()
src['time'] = src['time'].apply(lambda x: x.strftime("%Y-%m-%d"))
src = src.query("id == 3")
alt.Chart(
    src
).transform_filter(
    datum.glacial==False
).transform_window(
    rolling_mean='mean(elevation)',
    frame=[-5, 5],
    groupby=["id:O"]
).transform_filter(
    alt.datum.path_distance > 3
).transform_filter(
    alt.datum.path_distance < 315
).mark_line().encode(
    alt.X("path_distance:Q", title="Distance (m)", scale=alt.Scale(zero=False, 
    domain=[0,325], 
    nice=False)),
    alt.Y("rolling_mean:Q", title="Elevation (m)", scale=alt.Scale(zero=False, 
    domain=[1120, 1280], 
    nice=False)),
    alt.Color("time:O", scale=alt.Scale(scheme='turbo')),
).properties(
    width = 325,
    height = 200
).configure_legend(
    titleColor='black', 
    titleFontSize=12, 
    labelFontSize=16, 
    symbolStrokeWidth=4
).configure_axis(
    titleColor='black', 
    titleFontSize=14, 
    labelFontSize=16
)

alt.Chart(...)